#### Seq2Seq Model
https://towardsdatascience.com/seq2seq-model-in-tensorflow-ec0c557e560f

#### Bahdanau Attention mechanism
https://medium.com/analytics-vidhya/neural-machine-translation-using-bahdanau-attention-mechanism-d496c9be30c3

In [ ]:
import tensorflow as tf
tf.version.VERSION

In [ ]:
pip install tensorflow==1.15

In [1]:
import pandas as pd
import gzip
import codecs
import re
import time
import tensorflow as tf
import numpy as np

In [2]:
from tensorflow.python.ops.rnn_cell_impl import _zero_state_tensors
from tensorflow.python.layers.core import Dense
from tensorflow.contrib.seq2seq import TrainingHelper, GreedyEmbeddingHelper, BasicDecoder, dynamic_decode
from tensorflow.contrib.seq2seq import BahdanauAttention, AttentionWrapper, sequence_loss
from tensorflow.contrib.rnn import GRUCell, DropoutWrapper
TOKEN_GO = '<GO>'
TOKEN_EOS = '<EOS>'
TOKEN_PAD = '<PAD>'
TOKEN_UNK = '<UNK>'

#### Dropout wrapper 
https://stackoverflow.com/questions/45507315/what-exactly-does-tf-contrib-rnn-dropoutwrapper-in-tensorflow-do-three-cit

In [4]:
frdata=[]
endata=[]
with open('/Users/r.shyaamprasadh/Downloads/train_fr_lines.txt') as frfile:
    for li in frfile:
        frdata.append(li)
with open('/Users/r.shyaamprasadh/Downloads/train_en_lines.txt') as enfile:
    for li in enfile:
        endata.append(li)
mtdata = pd.DataFrame({'FR':frdata,'EN':endata})
mtdata['FR_len'] = mtdata['FR'].apply(lambda x: len(x.split(' ')))
mtdata['EN_len'] = mtdata['EN'].apply(lambda x: len(x.split(' ')))

In [5]:
mtdata

FR  \
0                 Voici Bill Lange. Je suis Dave Gallo.\n   
1       Nous allons vous raconter quelques histoires d...   
2       Nous avons des vidéos du Titanic parmi les plu...   
3       La vérité est que le Titanic -- même s'il cont...   
4       Le problème, je crois, est qu'on tient l'océan...   
...                                                   ...   
210992  Lorsque notre ambition est maitrisée, elle nou...   
210993  Lorsque notre ambition est débridée, elle nous...   
210994  Quand nos peurs sont débridées et amplifiées, ...   
210995  La leçon que j'aimerais que vous tiriez de ces...   
210996                                           Merci.\n   

                                                       EN  FR_len  EN_len  
0                   This is Bill Lange. I'm Dave Gallo.\n       7       7  
1       And we're going to tell you some stories from ...      11      14  
2       We've got some of the most incredible video of...      21      24  
3       The truth of the matter is that the Titanic --...      24      30  
4       And the problem, I think, is that we take the ...      10      13  
...                                                   ...     ...     ...  
210992  When our ambition is bounded, it leads us to w...      11      11  
210993  When our ambition is unbounded, it leads us to...      32      34  
210994  When our fears are unbounded and overblown, we...      12      12  
210995  The lesson I want to leave you with from these...      33      44  
210996                                       Thank you.\n       1       2  

[210997 rows x 4 columns]

In [6]:
mtdata_fr = []
for fr in mtdata.FR:
    mtdata_fr.append(fr)
mtdata_en = []
for en in mtdata.EN:
    mtdata_en.append(en)

In [7]:
mtdata_fr

['Voici Bill Lange. Je suis Dave Gallo.\n',
 'Nous allons vous raconter quelques histoires de la mer en vidéo.\n',
 "Nous avons des vidéos du Titanic parmi les plus spectaculaires jamais vues. et nous n'allons pas vous en montrer une image.\n",
 "La vérité est que le Titanic -- même s'il continue de battre toutes les records de recettes -- n'est pas l'histoire la plus passionnante.\n",
 "Le problème, je crois, est qu'on tient l'océan pour acquis.\n",
 'Quand vous y pensez, les océans représentent 75% de la planète.\n',
 "La plus grande partie de la planète est d'eau.\n",
 'La profondeur moyenne est environ 3,2 km.\n',
 "Une partie du problème, je pense, est qu'en étant sur la plage ou en regardant des images de l'océan, comme celles-ci, on voit cette grande étendue bleue, chatoyante, ça bouge, il y a des vagues, il y a du surf et il y a des marées, mais vous n'avez aucune idée de ce qui s'y cache.\n",
 'Il y existe les chaînes de montagnes les plus longues de la planète.\n',
 'La plupa

##### Count the words function 

In [8]:
def count_words(words_dict, text):
    for sentence in text:
        for word in sentence.split():
            if word not in words_dict:
                words_dict[word] = 1
            else:
                words_dict[word] += 1

In [9]:
word_counts_dict_fr = {}
word_counts_dict_en = {}
count_words(word_counts_dict_fr, mtdata_fr)
count_words(word_counts_dict_en, mtdata_en)

In [10]:
word_counts_dict_fr

{'Voici': 2513,
 'Bill': 136,
 'Lange.': 1,
 'Je': 13112,
 'suis': 6372,
 'Dave': 26,
 'Gallo.': 1,
 'Nous': 9965,
 'allons': 1056,
 'vous': 38142,
 'raconter': 437,
 'quelques': 2711,
 'histoires': 502,
 'de': 153715,
 'la': 79759,
 'mer': 271,
 'en': 43650,
 'vidéo.': 134,
 'avons': 10315,
 'des': 51842,
 'vidéos': 171,
 'du': 23046,
 'Titanic': 7,
 'parmi': 480,
 'les': 63699,
 'plus': 21265,
 'spectaculaires': 18,
 'jamais': 2551,
 'vues.': 19,
 'et': 76897,
 'nous': 38539,
 "n'allons": 55,
 'pas': 30264,
 'montrer': 1307,
 'une': 38877,
 'image.': 76,
 'La': 5980,
 'vérité': 242,
 'est': 29492,
 'que': 68798,
 'le': 64559,
 '--': 11833,
 'même': 6643,
 "s'il": 791,
 'continue': 243,
 'battre': 140,
 'toutes': 3136,
 'records': 15,
 'recettes': 30,
 "n'est": 5216,
 "l'histoire": 871,
 'passionnante.': 5,
 'Le': 5099,
 'problème,': 341,
 'je': 27920,
 'crois,': 169,
 "qu'on": 3900,
 'tient': 158,
 "l'océan": 186,
 'pour': 33108,
 'acquis.': 16,
 'Quand': 1823,
 'y': 14031,
 'pensez,

In [11]:
word_counts_dict_en

{'This': 6831,
 'is': 49754,
 'Bill': 131,
 'Lange.': 1,
 "I'm": 7199,
 'Dave': 27,
 'Gallo.': 1,
 'And': 36522,
 "we're": 4436,
 'going': 9403,
 'to': 101576,
 'tell': 2516,
 'you': 42684,
 'some': 6652,
 'stories': 527,
 'from': 12169,
 'the': 162600,
 'sea': 276,
 'here': 3671,
 'in': 59809,
 'video.': 101,
 "We've": 654,
 'got': 4608,
 'of': 94547,
 'most': 3910,
 'incredible': 427,
 'video': 642,
 'Titanic': 8,
 "that's": 6289,
 'ever': 1485,
 'been': 5504,
 'seen,': 56,
 'and': 86893,
 'not': 14175,
 'show': 1923,
 'any': 2742,
 'it.': 4340,
 'The': 9522,
 'truth': 237,
 'matter': 654,
 'that': 62904,
 '--': 20951,
 'even': 3777,
 'though': 561,
 "it's": 11708,
 'breaking': 77,
 'all': 13618,
 'sorts': 327,
 'box': 225,
 'office': 205,
 'records': 79,
 'exciting': 256,
 'story': 1197,
 'sea.': 66,
 'problem,': 288,
 'I': 54794,
 'think,': 816,
 'we': 37111,
 'take': 3794,
 'ocean': 298,
 'for': 22843,
 'granted.': 24,
 'When': 1798,
 'think': 7539,
 'about': 16679,
 'it,': 2863,


In [12]:
len(word_counts_dict_en) ##number of words in the english dictionary 

127479

In [13]:
len(word_counts_dict_fr) ##number of words in the french dictionary 

159523

In [14]:
word_counts_dict_en.items()

dict_items([('This', 6831), ('is', 49754), ('Bill', 131), ('Lange.', 1), ("I'm", 7199), ('Dave', 27), ('Gallo.', 1), ('And', 36522), ("we're", 4436), ('going', 9403), ('to', 101576), ('tell', 2516), ('you', 42684), ('some', 6652), ('stories', 527), ('from', 12169), ('the', 162600), ('sea', 276), ('here', 3671), ('in', 59809), ('video.', 101), ("We've", 654), ('got', 4608), ('of', 94547), ('most', 3910), ('incredible', 427), ('video', 642), ('Titanic', 8), ("that's", 6289), ('ever', 1485), ('been', 5504), ('seen,', 56), ('and', 86893), ('not', 14175), ('show', 1923), ('any', 2742), ('it.', 4340), ('The', 9522), ('truth', 237), ('matter', 654), ('that', 62904), ('--', 20951), ('even', 3777), ('though', 561), ("it's", 11708), ('breaking', 77), ('all', 13618), ('sorts', 327), ('box', 225), ('office', 205), ('records', 79), ('exciting', 256), ('story', 1197), ('sea.', 66), ('problem,', 288), ('I', 54794), ('think,', 816), ('we', 37111), ('take', 3794), ('ocean', 298), ('for', 22843), ('gran

In [15]:
word_counts_dict_en.keys()

dict_keys(['This', 'is', 'Bill', 'Lange.', "I'm", 'Dave', 'Gallo.', 'And', "we're", 'going', 'to', 'tell', 'you', 'some', 'stories', 'from', 'the', 'sea', 'here', 'in', 'video.', "We've", 'got', 'of', 'most', 'incredible', 'video', 'Titanic', "that's", 'ever', 'been', 'seen,', 'and', 'not', 'show', 'any', 'it.', 'The', 'truth', 'matter', 'that', '--', 'even', 'though', "it's", 'breaking', 'all', 'sorts', 'box', 'office', 'records', 'exciting', 'story', 'sea.', 'problem,', 'I', 'think,', 'we', 'take', 'ocean', 'for', 'granted.', 'When', 'think', 'about', 'it,', 'oceans', 'are', '75', 'percent', 'planet.', 'Most', 'planet', 'water.', 'average', 'depth', 'two', 'miles.', 'Part', 'stand', 'at', 'beach,', 'or', 'see', 'images', 'like', 'this', 'ocean,', 'look', 'out', 'great', 'big', 'blue', 'expanse,', 'shimmering', 'moving', "there's", 'waves', 'surf', 'tides,', 'but', 'have', 'no', 'idea', 'what', 'lies', 'there.', 'oceans,', 'there', 'longest', 'mountain', 'ranges', 'on', 'animals', 'oc

In [16]:
word_counts_dict_en.values()

dict_values([6831, 49754, 131, 1, 7199, 27, 1, 36522, 4436, 9403, 101576, 2516, 42684, 6652, 527, 12169, 162600, 276, 3671, 59809, 101, 654, 4608, 94547, 3910, 427, 642, 8, 6289, 1485, 5504, 56, 86893, 14175, 1923, 2742, 4340, 9522, 237, 654, 62904, 20951, 3777, 561, 11708, 77, 13618, 327, 225, 205, 79, 256, 1197, 66, 288, 54794, 816, 37111, 3794, 298, 22843, 24, 1798, 7539, 16679, 2863, 77, 21795, 101, 2220, 286, 327, 449, 348, 395, 60, 4177, 48, 40, 382, 15178, 30, 10569, 7271, 323, 11515, 30129, 91, 4188, 8350, 2038, 2003, 377, 1, 3, 566, 3514, 80, 10, 5, 11548, 21906, 4231, 1837, 16418, 99, 1401, 26, 7717, 27, 148, 9, 19443, 451, 34, 6, 11, 48, 328, 44, 1, 23, 122, 4772, 29352, 6, 7042, 215, 3, 509, 639, 9, 1, 5036, 5485, 1341, 209, 19617, 9896, 8897, 3808, 292, 5668, 115, 85381, 9828, 14, 1553, 8256, 328, 1162, 7657, 6540, 2851, 13, 8, 24, 80, 4670, 1, 6747, 443, 1275, 3, 5, 4, 3658, 586, 486, 22, 98, 11729, 3816, 44, 3420, 27, 15035, 1070, 5, 523, 8, 622, 125, 4031, 101, 4248, 77

### Embedding Matix

1. Build the embedding index for GloVe 6B 50 dimensions
2. Build the word2id and id2word mapping
3. Build the embedding matrix for both french and english 


In [17]:
def build_word_vector_matrix(vector_file):
    embedding_index = {}
    with codecs.open(vector_file, 'r', 'utf-8') as f:
        for i, line in enumerate(f):
            sr = line.split()
            if(len(sr)<26):
                continue
            word = sr[0]
            embedding = np.asarray(sr[1:], dtype='float32')
            embedding_index[word] = embedding
    return embedding_index

In [18]:
embeddings_index = build_word_vector_matrix('/Users/r.shyaamprasadh/Downloads/glove.6B.50d.txt')

In [19]:
embeddings_index

{'the': array([ 4.1800e-01,  2.4968e-01, -4.1242e-01,  1.2170e-01,  3.4527e-01,
        -4.4457e-02, -4.9688e-01, -1.7862e-01, -6.6023e-04, -6.5660e-01,
         2.7843e-01, -1.4767e-01, -5.5677e-01,  1.4658e-01, -9.5095e-03,
         1.1658e-02,  1.0204e-01, -1.2792e-01, -8.4430e-01, -1.2181e-01,
        -1.6801e-02, -3.3279e-01, -1.5520e-01, -2.3131e-01, -1.9181e-01,
        -1.8823e+00, -7.6746e-01,  9.9051e-02, -4.2125e-01, -1.9526e-01,
         4.0071e+00, -1.8594e-01, -5.2287e-01, -3.1681e-01,  5.9213e-04,
         7.4449e-03,  1.7778e-01, -1.5897e-01,  1.2041e-02, -5.4223e-02,
        -2.9871e-01, -1.5749e-01, -3.4758e-01, -4.5637e-02, -4.4251e-01,
         1.8785e-01,  2.7849e-03, -1.8411e-01, -1.1514e-01, -7.8581e-01],
       dtype=float32),
 ',': array([ 0.013441,  0.23682 , -0.16899 ,  0.40951 ,  0.63812 ,  0.47709 ,
        -0.42852 , -0.55641 , -0.364   , -0.23938 ,  0.13001 , -0.063734,
        -0.39575 , -0.48162 ,  0.23291 ,  0.090201, -0.13324 ,  0.078639,
        -0.4

In [20]:
def build_word2id_mapping(word_counts_dict):
    word2int = {} 
    count_threshold = 20
    value = 0
    for word, count in word_counts_dict.items():
        if count >= count_threshold or word in embeddings_index:
            word2int[word] = value
            value += 1
    print("Before special token",len(word2int))        
    special_codes = [TOKEN_UNK,TOKEN_PAD,TOKEN_EOS,TOKEN_GO]   

    for code in special_codes:
        word2int[code] = len(word2int)
        print("After special token",len(word2int))

    int2word = {}
    for word, value in word2int.items():
        int2word[value] = word
    return word2int,int2word
            

In [21]:
print("English Word2id mapping \n")
eng_word2int,eng_int2word = build_word2id_mapping(word_counts_dict_en)
print("\nFrench Word2id mapping\n ")
fre_word2int,fre_int2word = build_word2id_mapping(word_counts_dict_fr)

English Word2id mapping 

Before special token 39610
After special token 39611
After special token 39612
After special token 39613
After special token 39614

French Word2id mapping
 
Before special token 19704
After special token 19705
After special token 19706
After special token 19707
After special token 19708


In [22]:
eng_word2int

{'This': 0,
 'is': 1,
 'Bill': 2,
 "I'm": 3,
 'Dave': 4,
 'And': 5,
 "we're": 6,
 'going': 7,
 'to': 8,
 'tell': 9,
 'you': 10,
 'some': 11,
 'stories': 12,
 'from': 13,
 'the': 14,
 'sea': 15,
 'here': 16,
 'in': 17,
 'video.': 18,
 "We've": 19,
 'got': 20,
 'of': 21,
 'most': 22,
 'incredible': 23,
 'video': 24,
 "that's": 25,
 'ever': 26,
 'been': 27,
 'seen,': 28,
 'and': 29,
 'not': 30,
 'show': 31,
 'any': 32,
 'it.': 33,
 'The': 34,
 'truth': 35,
 'matter': 36,
 'that': 37,
 '--': 38,
 'even': 39,
 'though': 40,
 "it's": 41,
 'breaking': 42,
 'all': 43,
 'sorts': 44,
 'box': 45,
 'office': 46,
 'records': 47,
 'exciting': 48,
 'story': 49,
 'sea.': 50,
 'problem,': 51,
 'I': 52,
 'think,': 53,
 'we': 54,
 'take': 55,
 'ocean': 56,
 'for': 57,
 'granted.': 58,
 'When': 59,
 'think': 60,
 'about': 61,
 'it,': 62,
 'oceans': 63,
 'are': 64,
 '75': 65,
 'percent': 66,
 'planet.': 67,
 'Most': 68,
 'planet': 69,
 'water.': 70,
 'average': 71,
 'depth': 72,
 'two': 73,
 'miles.': 74,


In [23]:
eng_int2word

{0: 'This',
 1: 'is',
 2: 'Bill',
 3: "I'm",
 4: 'Dave',
 5: 'And',
 6: "we're",
 7: 'going',
 8: 'to',
 9: 'tell',
 10: 'you',
 11: 'some',
 12: 'stories',
 13: 'from',
 14: 'the',
 15: 'sea',
 16: 'here',
 17: 'in',
 18: 'video.',
 19: "We've",
 20: 'got',
 21: 'of',
 22: 'most',
 23: 'incredible',
 24: 'video',
 25: "that's",
 26: 'ever',
 27: 'been',
 28: 'seen,',
 29: 'and',
 30: 'not',
 31: 'show',
 32: 'any',
 33: 'it.',
 34: 'The',
 35: 'truth',
 36: 'matter',
 37: 'that',
 38: '--',
 39: 'even',
 40: 'though',
 41: "it's",
 42: 'breaking',
 43: 'all',
 44: 'sorts',
 45: 'box',
 46: 'office',
 47: 'records',
 48: 'exciting',
 49: 'story',
 50: 'sea.',
 51: 'problem,',
 52: 'I',
 53: 'think,',
 54: 'we',
 55: 'take',
 56: 'ocean',
 57: 'for',
 58: 'granted.',
 59: 'When',
 60: 'think',
 61: 'about',
 62: 'it,',
 63: 'oceans',
 64: 'are',
 65: '75',
 66: 'percent',
 67: 'planet.',
 68: 'Most',
 69: 'planet',
 70: 'water.',
 71: 'average',
 72: 'depth',
 73: 'two',
 74: 'miles.',


In [24]:
def build_embeddings(word2int):
    embedding_dim = 50
    j=0
    nwords = len(word2int)
    word_emb_matrix = np.zeros((nwords, embedding_dim), dtype=np.float32)
    for word, i in word2int.items():
        if word in embeddings_index:
            word_emb_matrix[i] = embeddings_index[word]
        else:
            j +=1
            new_embedding = np.array(np.random.uniform(-1.0, 1.0, embedding_dim))
            word_emb_matrix[i] = new_embedding
    print (j/nwords)
    return word_emb_matrix

In [25]:
fr_embeddings_matrix = build_embeddings(fre_word2int)
en_embeddings_matrix = build_embeddings(eng_word2int)

0.45961031053379336
0.11912455192608673


In [26]:
fr_embeddings_matrix

array([[-0.7066877 , -0.32136256,  0.91148925, ...,  0.39200145,
        -0.21735014, -0.8064226 ],
       [ 0.03311572, -0.45651105, -0.01834886, ...,  0.7515229 ,
         0.2683725 , -0.9653974 ],
       [-0.9651023 , -0.25517818, -0.6061798 , ..., -0.6424147 ,
         0.47061595,  0.5244318 ],
       ...,
       [-0.5846007 , -0.6184489 ,  0.44450957, ..., -0.29673958,
         0.9007911 , -0.04814348],
       [-0.8279828 , -0.03951681,  0.15047447, ..., -0.12623128,
        -0.17100184,  0.48975828],
       [ 0.5025656 ,  0.00532666,  0.05739624, ...,  0.3422232 ,
        -0.8818843 , -0.4680588 ]], dtype=float32)

In [27]:
en_embeddings_matrix

array([[-0.44456866,  0.9331102 ,  0.31280386, ..., -0.12263589,
        -0.2731373 , -0.2074989 ],
       [ 0.6185    ,  0.64254   , -0.46552   , ..., -0.27557   ,
         0.30899   ,  0.48497   ],
       [-0.376001  , -0.12668906,  0.2835559 , ..., -0.16434298,
        -0.710456  ,  0.6496426 ],
       ...,
       [-0.30207482,  0.7468813 , -0.22130777, ..., -0.210952  ,
        -0.82664114, -0.54704607],
       [-0.35225472,  0.7857177 ,  0.06963034, ...,  0.13196185,
        -0.61921114,  0.7708792 ],
       [ 0.5467084 ,  0.55333596,  0.2438457 , ...,  0.09432585,
        -0.09463147, -0.6952908 ]], dtype=float32)

##### Length of embedding matrix 

In [28]:
print('Length of french embeddings:',len(fr_embeddings_matrix))

Length of french embeddings: 19708


In [29]:
print('Length of english embeddings:',len(en_embeddings_matrix))

Length of english embeddings: 39614


#### Convert sentence to ids 

Parameters : Text data (English/French), word2int dicitonary

In [30]:
def convert_sentence_to_ids(text, word2int, eos=False):
    wordints = []
    word_count = 0
    for sentence in text:
        sentence2ints = []
        for word in sentence.split():
            word_count += 1
            if word in word2int:
                sentence2ints.append(word2int[word])
            else:
                sentence2ints.append(word2int[TOKEN_UNK])
        if eos:
            sentence2ints.append(word2int[TOKEN_EOS])
        wordints.append(sentence2ints)
    return wordints, word_count

In [31]:
id_fr, word_count_fr = convert_sentence_to_ids(mtdata_fr, fre_word2int)
id_en, word_count_en = convert_sentence_to_ids(mtdata_en, eng_word2int, eos=True)
print("Word counts",word_count_fr,word_count_en)
print("Number of sentences (english/french)",len(id_en),len(id_fr))

Word counts 3790299 3611102
Number of sentences (english/french) 210997 210997


In [32]:
id_en

[[0, 1, 2, 39610, 3, 4, 39610, 39612],
 [5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 39612],
 [19,
  20,
  11,
  21,
  14,
  22,
  23,
  24,
  21,
  39610,
  25,
  26,
  27,
  28,
  29,
  6,
  30,
  7,
  8,
  31,
  10,
  32,
  21,
  33,
  39612],
 [34,
  35,
  21,
  14,
  36,
  1,
  37,
  14,
  39610,
  38,
  39,
  40,
  41,
  42,
  43,
  44,
  21,
  45,
  46,
  47,
  38,
  41,
  30,
  14,
  22,
  48,
  49,
  13,
  14,
  50,
  39612],
 [5, 14, 51, 52, 53, 1, 37, 54, 55, 14, 56, 57, 58, 39612],
 [59, 10, 60, 61, 62, 14, 63, 64, 65, 66, 21, 14, 67, 39612],
 [68, 21, 14, 69, 1, 56, 70, 39612],
 [34, 71, 72, 1, 61, 73, 74, 39612],
 [75,
  21,
  14,
  51,
  52,
  53,
  1,
  54,
  76,
  77,
  14,
  78,
  79,
  54,
  80,
  81,
  82,
  83,
  21,
  14,
  84,
  29,
  10,
  85,
  86,
  77,
  83,
  87,
  88,
  89,
  39610,
  29,
  41,
  90,
  29,
  41,
  91,
  29,
  92,
  93,
  29,
  92,
  94,
  29,
  92,
  39610,
  95,
  10,
  96,
  97,
  98,
  57,
  99,
  100,
  17,
  101,
  39612],
 [5, 

##### Filtered sentences

In [33]:
def unknown_tokens(sentence, word2int):
    unk_token_count = 0
    for word in sentence:
        if word == word2int[TOKEN_UNK]:
            unk_token_count += 1
    return unk_token_count

In [34]:
en_filtered = []
fr_filtered = []
max_en_length = int(mtdata.EN_len.max())
max_fr_length = int(mtdata.FR_len.max())
print(max_en_length,max_fr_length)
min_length = 4
unknown_token_en_limit = 10
unknown_token_fr_limit = 10
j=0
k=0

for count,text in enumerate(id_en):
    unknown_token_en = unknown_tokens(id_en[count],eng_word2int)
    unknown_token_fr = unknown_tokens(id_fr[count],fre_word2int)
    en_len = len(id_en[count])
    fr_len = len(id_fr[count])
    if( (unknown_token_en>unknown_token_en_limit) or (unknown_token_fr>unknown_token_fr_limit) or 
       (en_len<min_length) or (fr_len<min_length) ):
        continue
    fr_filtered.append(id_fr[count])
    en_filtered.append(id_en[count])
print("Length of filtered french/english sentences: ", len(fr_filtered), len(en_filtered) )

513 638
Length of filtered french/english sentences:  200404 200404


# Building the  Seq-Seq model

#### Create the placeholders 

In [35]:
def model_ip():
    inputs_data = tf.placeholder(tf.int32, [None, None], name='input_data')
    targets = tf.placeholder(tf.int32, [None, None], name='targets')
    learning_rate = tf.placeholder(tf.float32, name='learning_rate')
    dropout_probs = tf.placeholder(tf.float32, name='dropout_probs')
    en_len = tf.placeholder(tf.int32, (None,), name='en_len')
    max_en_len = tf.reduce_max(en_len, name='max_en_len')
    fr_len = tf.placeholder(tf.int32, (None,), name='fr_len')
    return inputs_data, targets, learning_rate, dropout_probs, en_len, max_en_len, fr_len  

#### Process the encoding ip
Arguments : Englisht_text, English word2int, batch_size 
Striding slice : https://medium.com/@mozesr/python-matrix-strides-numpy-tensorflow-5f73f6fa1aca

In [36]:
def process_encoding_ip(target_data, word2int, batch_size):
    ending = tf.strided_slice(target_data, [0, 0], [batch_size, -1], [1, 1])
    decoding_input = tf.concat([tf.fill([batch_size, 1], word2int[TOKEN_GO]), ending], 1)
    return decoding_input

#### Instance to create RNN cell 

In [37]:
def get_rnn_cell(rnn_cell_size,dropout_prob):
    rnn_c = GRUCell(rnn_cell_size)
    rnn_c = DropoutWrapper(rnn_c, input_keep_prob = dropout_prob)
    return rnn_c


### Create the encoding layer 

**Arguments:**

Number of Units in RNN

Sequence length = Length of french sentences

Number of layers, 

RNN inputs = encoding_embeded_input

dropout probabilites 

**Output :**

Return sequences and Return states 

https://machinelearningmastery.com/return-sequences-and-return-states-for-lstms-in-keras/

In [38]:
def encoding_layer(rnn_cell_size, sequence_len, n_layers, rnn_inputs, dropout_prob):
    for l in range(n_layers):
        with tf.variable_scope('encoding_l_{}'.format(l)):
            rnn_fw = get_rnn_cell(rnn_cell_size,dropout_prob)
            rnn_bw = get_rnn_cell(rnn_cell_size,dropout_prob)
            encoding_output, encoding_state = tf.nn.bidirectional_dynamic_rnn(rnn_fw, rnn_bw, 
                                                                    rnn_inputs,
                                                                    sequence_len,
                                                                    dtype=tf.float32)
    encoding_output = tf.concat(encoding_output,2)
    return encoding_output, encoding_state

### Create the decoding layer 

Step 1 : Create the training process 
     
Step 2 : Create the inference process 

Source : https://towardsdatascience.com/sequence-to-sequence-models-from-rnn-to-transformers-e24097069639

Each process returns logits :

https://stackoverflow.com/questions/41455101/what-is-the-meaning-of-the-word-logits-in-tensorflow

### Training process

**Arguments:**

1) **decoding_embed_input** - o/p of tf.nn.embedding_lookup(embeddings_matrix of english, decoding_input).

                 Embedding_lookup function retrieves rows of the embedding matrix tensor
                 Decoding_input is the  o/p of process encoding input function (its actually ground truth)
   
  
2) **en_len**  place in memory where we will store value later on


3) **decoding_cell**  o/p of attention wrapper function 


4) **initial state** inititate the attention wrapper into zero_state 

5) **op_layer** o/p from dense layer

6) **v_size** Positive integer, dimensionality of the output space

7) **max_en_length** maximum of metadata_english sentence length 


*******************


**TrainingHelper**

A helper for use during training.  Only reads inputs. Returned sample_ids are the argmax of the RNN output logits.


**BasicDecoder**

BasicDecoder builds the decoder model. It means it connects the RNN layer(s) on the decoder side and the input prepared by TrainingHelper.



**Dynamic decode**

Dynamic_decode unrolls the decoder model so that actual prediction can be retrieved by BasicDecoder for each time steps.


In [39]:
def training_decoding_layer(decoding_embed_input, en_len, decoding_cell, initial_state, op_layer, 
                            v_size, max_en_len):
    helper = TrainingHelper(inputs=decoding_embed_input,sequence_length=en_len, time_major=False)
    dec = BasicDecoder(decoding_cell,helper,initial_state,op_layer) 
    logits, _, _ = dynamic_decode(dec,output_time_major=False,impute_finished=True, 
                                  maximum_iterations=max_en_len)
    return logits

### Inference process

**Arguments:**

1) **Embeddings** is en_embeddings_matrix

2) **Start token** and **End token** are word2int[TOKEN_GO],word2int[TOKEN_EOS]


3) **decoding_cell**  o/p of attention wrapper function 


4) **initial state** inititate the attention wrapper into zero_state 


5) **op_layer** o/p from dense layer


6) **max_en_length** maximum of metadata_english sentence length 

7) **batch_size** number of training example in the iteration

    

In [40]:
def inference_decoding_layer(embeddings, start_token, end_token, decoding_cell, initial_state, op_layer,
                             max_en_len, batch_size):
    
    start_tokens = tf.tile(tf.constant([start_token], dtype=tf.int32), [batch_size], name='start_tokens')
    inf_helper = GreedyEmbeddingHelper(embeddings,start_tokens,end_token)
    inf_decoder = BasicDecoder(decoding_cell,inf_helper,initial_state,op_layer)       
    inf_logits, _, _ = dynamic_decode(inf_decoder,output_time_major=False,impute_finished=True,
                                                            maximum_iterations=max_en_len)
    return inf_logits

### Decoding Layer 


Steps 1: For every RNN layer create the GRU cell with units = RNN len

Steps 2: Call the Bahdanau Attention

Step 3: Intialize the states

Step 4: Call the training and inference process 

In [41]:
def decoding_layer(decoding_embed_inp, embeddings, encoding_op, encoding_st, v_size, fr_len, 
                   en_len,max_en_len, rnn_cell_size, word2int, dropout_prob, batch_size, n_layers):
    
    for l in range(n_layers):
        with tf.variable_scope('dec_rnn_layer_{}'.format(l)):
            gru = tf.contrib.rnn.GRUCell(rnn_len)
            decoding_cell = tf.contrib.rnn.DropoutWrapper(gru,input_keep_prob = dropout_prob)
    out_l = Dense(v_size, kernel_initializer = tf.truncated_normal_initializer(mean = 0.0, stddev=0.1))
    
    attention = BahdanauAttention(rnn_cell_size, encoding_op,fr_len,normalize=False,name='BahdanauAttention')
    decoding_cell =  AttentionWrapper(decoding_cell,attention,rnn_len)
    attention_zero_state = decoding_cell.zero_state(batch_size , tf.float32 )
    attention_zero_state = attention_zero_state.clone(cell_state = encoding_st[0])
    with tf.variable_scope("decoding_layer"):
        logits_tr = training_decoding_layer(decoding_embed_inp, en_len,decoding_cell,attention_zero_state,out_l,
                                            v_size,max_en_len)      
                                                                                                
    with tf.variable_scope("decoding_layer", reuse=True):
        logits_inf = inference_decoding_layer(embeddings,word2int[TOKEN_GO],word2int[TOKEN_EOS],decoding_cell,  
                                              attention_zero_state,out_l,max_en_len,batch_size)       
                                                    
    return logits_tr, logits_inf

### Seq-Seq Model 

In [42]:
def seq2seq_model(input_data, target_en_data, dropout_prob, fr_len, en_len, max_en_len, 
                  v_size, rnn_cell_size, n_layers, word2int_en, batch_size):
    
    input_word_embeddings = tf.Variable(fr_embeddings_matrix, name="input_word_embeddings")
    encoding_embed_input = tf.nn.embedding_lookup(input_word_embeddings, input_data)
    encoding_op, encoding_st = encoding_layer(rnn_cell_size, fr_len, n_layers, encoding_embed_input, dropout_prob)
    
    decoding_input = process_encoding_ip(target_en_data, word2int_en, batch_size)
    decoding_embed_input = tf.nn.embedding_lookup(en_embeddings_matrix, decoding_input)
    
    tr_logits, inf_logits  = decoding_layer(decoding_embed_input,en_embeddings_matrix,encoding_op,
                                            encoding_st,v_size,fr_len,en_len,max_en_len,rnn_cell_size,         
                                            word2int_en,dropout_prob,batch_size,n_layers)        
 
    return tr_logits, inf_logits
                                                                                                 

### Build Graph + Define Loss, Optimizer w/AdamOptimizer

In [43]:
epochs = 20
batch_size = 64
rnn_len = 256
n_layers = 2
lr = 0.005
dr_prob = 0.75
logs_path='/Users/r.shyaamprasadh/Downloads/tmp/models/'

##### Why we have to reverse ?

https://stackoverflow.com/questions/51003992/why-do-we-reverse-input-when-feeding-in-seq2seq-model-in-tensorflow-tf-reverse

##### Why we have to use identity ?
https://stackoverflow.com/questions/49880372/what-is-the-difference-between-y-x-and-y-tf-identityx-in-tensorflow

In [44]:
train_graph = tf.Graph()
with train_graph.as_default():
    
    input_data, targets, learning_rate, dropout_probs, en_len, max_en_len, fr_len = model_ip()

    logits_tr, logits_inf = seq2seq_model(tf.reverse(input_data, [-1]),
                                                      targets, 
                                                      dropout_probs,   
                                                      fr_len,
                                                      en_len,
                                                      max_en_len,
                                                      len(eng_word2int)+1,
                                                      rnn_len, 
                                                      n_layers, 
                                                      eng_word2int,
                                                      batch_size)
    
    logits_tr = tf.identity(logits_tr.rnn_output, 'logits_tr')
    logits_inf = tf.identity(logits_inf.sample_id, name='predictions')
    
    seq_masks = tf.sequence_mask(en_len, max_en_len, dtype=tf.float32, name='masks')

    with tf.name_scope("optimizer"):
        tr_cost = sequence_loss(logits_tr,targets,seq_masks)
        optimizer = tf.train.AdamOptimizer(learning_rate)
        gradients = optimizer.compute_gradients(tr_cost)
        capped_gradients = [(tf.clip_by_value(gradient, -5., 5.), var) for gradient, var in gradients 
                        if gradient is not None]
        train_op = optimizer.apply_gradients(capped_gradients)
    tf.summary.scalar("cost", tr_cost)
print("Graph created.")

Instructions for updating:
This class is equivalent as tf.keras.layers.GRUCell, and will be replaced by that in Tensorflow 2.0.
Instructions for updating:
Please use `keras.layers.Bidirectional(keras.layers.RNN(cell))`, which is equivalent to this API
Instructions for updating:
Please use `keras.layers.RNN(cell)`, which is equivalent to this API
Instructions for updating:
Please use `layer.add_weight` method instead.
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where
The TensorFlow contrib module will not be included in TensorFlow 2.0.
For more information, please see:
  * https://github.com/tensorflow/community/blob/master/rfcs/20180907-contrib-sunset.md
  * https://github.com/tensorflow/addons
  * https://gith

#### Training the Model 

In [45]:
def pad_sentences(sentences_batch,word2int):
    max_sentence = max([len(sentence) for sentence in sentences_batch])
    return [sentence + [word2int[TOKEN_PAD]] * (max_sentence - len(sentence)) for sentence in sentences_batch]

In [46]:
def get_batches(en_text, fr_text, batch_size):
    for batch_idx in range(0, len(fr_text)//batch_size):
        start_idx = batch_idx * batch_size
        en_batch = en_text[start_idx:start_idx + batch_size]
        fr_batch = fr_text[start_idx:start_idx + batch_size]
        pad_en_batch = np.array(pad_sentences(en_batch, eng_word2int))
        pad_fr_batch = np.array(pad_sentences(fr_batch,fre_word2int))
        pad_en_lens = []
        for en_b in pad_en_batch:
            pad_en_lens.append(len(en_b))
        
        pad_fr_lens = []
        for fr_b in pad_fr_batch:
            pad_fr_lens.append(len(fr_b))
        
        yield pad_en_batch, pad_fr_batch, pad_en_lens, pad_fr_lens

In [47]:
min_learning_rate = 0.0006
display_step = 20 
stop_early_count = 0 
stop_early_max_count = 3 
per_epoch = 3 


update_loss = 0 
batch_loss = 0
summary_update_loss = [] 

en_train = en_filtered[0:30000]
fr_train = fr_filtered[0:30000]
update_check = (len(fr_train)//batch_size//per_epoch)-1
checkpoint = logs_path + 'best_so_far_model.ckpt' 
with tf.Session(graph=train_graph) as sess:
    tf_summary_writer = tf.summary.FileWriter(logs_path, graph=train_graph)
    merged_summary_op = tf.summary.merge_all()
    sess.run(tf.global_variables_initializer())
    for epoch_i in range(1, epochs+1):
        update_loss = 0
        batch_loss = 0
        for batch_i, (en_batch, fr_batch, en_text_len, fr_text_len) in enumerate(
                get_batches(en_train, fr_train, batch_size)):
            before = time.time()
            _,loss,summary = sess.run(
                [train_op, tr_cost,merged_summary_op],
                {input_data: fr_batch,
                 targets: en_batch,
                 learning_rate: lr,
                 en_len: en_text_len,
                 fr_len: fr_text_len,
                 dropout_probs: dr_prob})
            batch_loss += loss
            update_loss += loss
            after = time.time()
            batch_time = after - before
            tf_summary_writer.add_summary(summary, epoch_i * batch_size + batch_i)
            if batch_i % display_step == 0 and batch_i > 0:
                print('** Epoch {:>3}/{} Batch {:>4}/{} - Batch Loss: {:>6.3f}, seconds: {:>4.2f}'
                      .format(epoch_i,
                              epochs, 
                              batch_i, 
                              len(fr_filtered) // batch_size, 
                              batch_loss / display_step, 
                              batch_time*display_step))
                batch_loss = 0

            if batch_i % update_check == 0 and batch_i > 0:
                print("Average loss:", round(update_loss/update_check,3))
                summary_update_loss.append(update_loss)
                
                if update_loss <= min(summary_update_loss):
                    print('Saving model') 
                    stop_early_count = 0
                    saver = tf.train.Saver() 
                    saver.save(sess, checkpoint)

                else:
                    print("No Improvement.")
                    stop_early_count += 1
                    if stop_early_count == stop_early_max_count:
                        break
                update_loss = 0

        if stop_early_count == stop_early_max_count:
            print("Stopping Training.")
            break

** Epoch   1/20 Batch   20/3131 - Batch Loss:  6.327, seconds: 85.49
** Epoch   1/20 Batch   40/3131 - Batch Loss:  2.370, seconds: 73.04
** Epoch   1/20 Batch   60/3131 - Batch Loss:  2.384, seconds: 74.67
** Epoch   1/20 Batch   80/3131 - Batch Loss:  2.027, seconds: 93.74
** Epoch   1/20 Batch  100/3131 - Batch Loss:  2.148, seconds: 64.10
** Epoch   1/20 Batch  120/3131 - Batch Loss:  2.189, seconds: 97.34
** Epoch   1/20 Batch  140/3131 - Batch Loss:  2.383, seconds: 74.42
Average loss: 2.768
Saving model
** Epoch   1/20 Batch  160/3131 - Batch Loss:  2.223, seconds: 77.24
** Epoch   1/20 Batch  180/3131 - Batch Loss:  2.030, seconds: 65.80
** Epoch   1/20 Batch  200/3131 - Batch Loss:  2.189, seconds: 98.87
** Epoch   1/20 Batch  220/3131 - Batch Loss:  2.122, seconds: 45.95
** Epoch   1/20 Batch  240/3131 - Batch Loss:  2.012, seconds: 75.95
** Epoch   1/20 Batch  260/3131 - Batch Loss:  1.955, seconds: 154.06
** Epoch   1/20 Batch  280/3131 - Batch Loss:  2.015, seconds: 66.59


KeyboardInterrupt: 

In [48]:
random = np.random.randint(0,3000)
fr_text = fr_filtered[random]

checkpoint = logs_path + 'best_so_far_model.ckpt'

loaded_graph = tf.Graph()
with tf.Session(graph=loaded_graph) as sess:
    loader = tf.train.import_meta_graph(checkpoint + '.meta')
    loader.restore(sess, checkpoint)
    input_data = loaded_graph.get_tensor_by_name('input_data:0')
    logits = loaded_graph.get_tensor_by_name('predictions:0')
    fr_length = loaded_graph.get_tensor_by_name('fr_len:0')
    en_length = loaded_graph.get_tensor_by_name('en_len:0')
    dropout_prob = loaded_graph.get_tensor_by_name('dropout_probs:0')
    result_logits = sess.run(logits, {input_data: [fr_text]*batch_size, 
                                      en_length: [len(fr_text)], 
                                      fr_length: [len(fr_text)]*batch_size,
                                      dropout_prob: 1.0}) 

INFO:tensorflow:Restoring parameters from /Users/r.shyaamprasadh/Downloads/tmp/models/best_so_far_model.ckpt


In [49]:
random = np.random.randint(0,3000)
fr_text = fr_filtered[random]

checkpoint = logs_path + 'best_so_far_model.ckpt'

loaded_graph = tf.Graph()
with tf.Session(graph=loaded_graph) as sess:
    loader = tf.train.import_meta_graph(checkpoint + '.meta')
    loader.restore(sess, checkpoint)
    input_data = loaded_graph.get_tensor_by_name('input_data:0')
    logits = loaded_graph.get_tensor_by_name('predictions:0')
    fr_length = loaded_graph.get_tensor_by_name('fr_len:0')
    en_length = loaded_graph.get_tensor_by_name('en_len:0')
    dropout_prob = loaded_graph.get_tensor_by_name('dropout_probs:0')
    result_logits = sess.run(logits, {input_data: [fr_text]*batch_size, 
                                      en_length: [len(fr_text)], 
                                      fr_length: [len(fr_text)]*batch_size,
                                      dropout_prob: 1.0})[10] 

pad = eng_word2int[TOKEN_PAD] 

#print('\nOriginal Text:', input_sentence)

print('\nFrench Text')
print('  Word Ids:    {}'.format([i for i in fr_text]))
print('  Input Words: {}'.format(" ".join( [fre_int2word[i] for i in fr_text ] )))

print('\nEnglish Text')
print('  Word Ids:       {}'.format([i for i in result_logits if i != pad]))
print('  Response Words: {}'.format(" ".join( [eng_int2word[i]for i in result_logits if i!=pad] )))
print(' Ground Truth: {}'.format(" ".join( [eng_int2word[i] for i in en_filtered[random]] )))

INFO:tensorflow:Restoring parameters from /Users/r.shyaamprasadh/Downloads/tmp/models/best_so_far_model.ckpt

French Text
  Word Ids:    [559, 1245, 1246, 19, 126, 11, 1247]
  Input Words: Un exemple rapide du monde de l'entreprise.

English Text
  Word Ids:       [489, 1247, 1247, 21, 14, 304, 21]
  Response Words: A example example of the world of
 Ground Truth: <UNK> example from the corporate world. <EOS>


In [50]:
from nltk.translate.bleu_score import corpus_bleu

In [54]:
french_comp=[fre_int2word[i] for i in fr_text ]

In [56]:
eng_comp=[eng_int2word[i]for i in result_logits if i!=pad]

In [61]:
score = corpus_bleu(french_comp, eng_comp,weights=(1, 0, 0, 0))
print(score)

0.37037037037037035
